In [1]:
# Import required libraries 

import os
import h5py
import numpy as np
import pandas as pd
import holoviews as hv
import time
import psutil
from scipy.interpolate import interp1d

In [2]:
inDir = os.getcwd() + os.sep  # Set input directory to the current working directory

In [3]:
gediFiles = [g for g in os.listdir() if g.startswith('GEDI01_B') and g.endswith('.h5')]  # List all GEDI L1B .h5 files in inDir

In [4]:
L1B = 'GEDI01_B_2019170155833_O02932_T02267_02_003_01.h5' # Specify Level 1B data file name

In [5]:
gediL1B = h5py.File(L1B, 'r')  # Read file using h5py

In [6]:
beamNames = [g for g in gediL1B.keys() if g.startswith('BEAM')]
beam_numbers = beamNames

In [7]:
for g in gediL1B['BEAM0000'].attrs: print(g)

description
wp-l1a-to-l1b_githash
wp-l1a-to-l1b_version


In [8]:
for b in beamNames: 
    print(f"{b} is a {gediL1B[b].attrs['description']}")

BEAM0000 is a Coverage beam
BEAM0001 is a Coverage beam
BEAM0010 is a Coverage beam
BEAM0011 is a Coverage beam
BEAM0101 is a Full power beam
BEAM0110 is a Full power beam
BEAM1000 is a Full power beam
BEAM1011 is a Full power beam


In [9]:
beamNames = ['BEAM0110']

In [10]:
gediL1B_objs = []
gediL1B.visit(gediL1B_objs.append)                                           # Retrieve list of datasets
gediSDS = [o for o in gediL1B_objs if isinstance(gediL1B[o], h5py.Dataset)]  # Search for relevant SDS inside data file
[i for i in gediSDS if beamNames[0] in i][0:10]                              # Print the first 10 datasets for selected beam

['BEAM0110/all_samples_sum',
 'BEAM0110/ancillary/master_time_epoch',
 'BEAM0110/ancillary/mean_samples',
 'BEAM0110/ancillary/smoothing_width',
 'BEAM0110/beam',
 'BEAM0110/channel',
 'BEAM0110/geolocation/altitude_instrument',
 'BEAM0110/geolocation/altitude_instrument_error',
 'BEAM0110/geolocation/bounce_time_offset_bin0',
 'BEAM0110/geolocation/bounce_time_offset_bin0_error']

In [11]:
lonSample, latSample, shotSample, srfSample, degradeSample, beamSample = [], [], [], [], [], []  # Set up lists to store data

# Open the SDS
lats = gediL1B[f'{beamNames[0]}/geolocation/latitude_bin0'][()]
lons = gediL1B[f'{beamNames[0]}/geolocation/longitude_bin0'][()]
shots = gediL1B[f'{beamNames[0]}/shot_number'][()]
srf = gediL1B[f'{beamNames[0]}/stale_return_flag'][()]
degrade = gediL1B[f'{beamNames[0]}/geolocation/degrade'][()]

# Take every 100th shot and append to list
for i in range(len(shots)):
    if i % 100 == 0:
        shotSample.append(str(shots[i]))
        lonSample.append(lons[i])
        latSample.append(lats[i])
        srfSample.append(srf[i])
        degradeSample.append(degrade[i])
        beamSample.append(beamNames[0])
            
# Write all of the sample shots to a dataframe
latslons = pd.DataFrame({'Beam': beamSample, 'Shot Number': shotSample, 'Longitude': lonSample, 'Latitude': latSample,
                         'Stale Return Flag': srfSample, 'Degrade': degradeSample})

shot_numbers = shotSample

latslons

Beam        Shot Number   Longitude   Latitude  Stale Return Flag  \
0     BEAM0110  29320618800000001  111.996300 -51.803868                  1   
1     BEAM0110  29320604600000101  112.039132 -51.803905                  1   
2     BEAM0110  29320614600000201  112.080271 -51.803836                  1   
3     BEAM0110  29320600400000301  112.121445 -51.803737                  1   
4     BEAM0110  29320610400000401  112.162622 -51.803621                  1   
...        ...                ...         ...        ...                ...   
9792  BEAM0110  29320617400979201   88.208452 -51.803578                  1   
9793  BEAM0110  29320603200979301   88.249610 -51.803614                  1   
9794  BEAM0110  29320613200979401   88.290753 -51.803581                  1   
9795  BEAM0110  29320623200979501   88.331913 -51.803548                  1   
9796  BEAM0110  29320609000979601   88.373089 -51.803506                  1   

      Degrade  
0           0  
1           0  
2           0  
3           0  
4           0  
...       ...  
9792        0  
9793        0  
9794        0  
9795        0  
9796        0  

[9797 rows x 6 columns]

In [12]:
wvDF_array = []

j = 0

for beam in beam_numbers:
    lonSample, latSample, shotSample, srfSample, degradeSample, beamSample = [], [], [], [], [], []  # Set up lists to store data

    # Open the SDS
    lats = gediL1B[f'{beam}/geolocation/latitude_bin0'][()]
    lons = gediL1B[f'{beam}/geolocation/longitude_bin0'][()]
    shots = gediL1B[f'{beam}/shot_number'][()]
    srf = gediL1B[f'{beam}/stale_return_flag'][()]
    degrade = gediL1B[f'{beam}/geolocation/degrade'][()]

    # Take every 100th shot and append to list
    for i in range(len(shots)):
        if i % 100 == 0:
            shotSample.append(str(shots[i]))
            lonSample.append(lons[i])
            latSample.append(lats[i])
            srfSample.append(srf[i])
            degradeSample.append(degrade[i])
            beamSample.append(beam)

    # Write all of the sample shots to a dataframe
    latslons = pd.DataFrame({'Beam': beamSample, 'Shot Number': shotSample, 'Longitude': lonSample, 'Latitude': latSample,
                             'Stale Return Flag': srfSample, 'Degrade': degradeSample})

    shot_numbers = shotSample
    
    wvDF_beam = []
    
    index1 = 0
    
    for shot in shot_numbers:
        
        index = np.where(gediL1B[f'{beam}/shot_number'][()]==int(shot))[0][0]  # Set the index for the shot identified above

        sdsCount = gediL1B[[g for g in gediSDS if g.endswith('/rx_sample_count') and beam in g][0]]
        sdsStart = gediL1B[[g for g in gediSDS if g.endswith('/rx_sample_start_index') and beam in g][0]]
        sdsWaveform = [g for g in gediSDS if g.endswith('/rxwaveform') and beam in g][0]

        wfCount = sdsCount[index]           # Number of samples in the waveform
        wfStart = int(sdsStart[index] - 1)  # Subtract one because python array indexing starts at 0 not 1

        wfShot = gediL1B[f'{beam}/shot_number'][index]
        wfLat = gediL1B[f'{beam}/geolocation/latitude_bin0'][index]
        wfLon = gediL1B[f'{beam}/geolocation/longitude_bin0'][index]

        # Grab the elevation recorded at the start and end of the full waveform capture
        zStart = gediL1B[f'{beam}/geolocation/elevation_bin0'][index]   # Height of the start of the rx window
        zEnd = gediL1B[f'{beam}/geolocation/elevation_lastbin'][index]  # Height of the end of the rx window

        waveform = gediL1B[sdsWaveform][wfStart: wfStart + wfCount]

        zStretch = np.add(zEnd, np.multiply(range(wfCount, 0, -1), ((zStart - zEnd) / int(wfCount))))

        wvDF = pd.DataFrame({'Amplitude (DN)': waveform, 'Elevation (m)': zStretch})
        hv.Curve(wvDF)
        

        wvDF_beam.append(wvDF)
        
        print(j)
        j+=1
        
    wvDF_array.append(wvDF_beam)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1862
1863
1864
1865
1866
1867
1868
1869
1870
1871
1872
1873
1874
1875
1876
1877
1878
1879
1880
1881
1882
1883
1884
1885
1886
1887
1888
1889
1890
1891
1892
1893
1894
1895
1896
1897
1898
1899
1900
1901
1902
1903
1904
1905
1906
1907
1908
1909
1910
1911
1912
1913
1914
1915
1916
1917
1918
1919
1920
1921
1922
1923
1924
1925
1926
1927
1928
1929
1930
1931
1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061


3502
3503
3504
3505
3506
3507
3508
3509
3510
3511
3512
3513
3514
3515
3516
3517
3518
3519
3520
3521
3522
3523
3524
3525
3526
3527
3528
3529
3530
3531
3532
3533
3534
3535
3536
3537
3538
3539
3540
3541
3542
3543
3544
3545
3546
3547
3548
3549
3550
3551
3552
3553
3554
3555
3556
3557
3558
3559
3560
3561
3562
3563
3564
3565
3566
3567
3568
3569
3570
3571
3572
3573
3574
3575
3576
3577
3578
3579
3580
3581
3582
3583
3584
3585
3586
3587
3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701


5142
5143
5144
5145
5146
5147
5148
5149
5150
5151
5152
5153
5154
5155
5156
5157
5158
5159
5160
5161
5162
5163
5164
5165
5166
5167
5168
5169
5170
5171
5172
5173
5174
5175
5176
5177
5178
5179
5180
5181
5182
5183
5184
5185
5186
5187
5188
5189
5190
5191
5192
5193
5194
5195
5196
5197
5198
5199
5200
5201
5202
5203
5204
5205
5206
5207
5208
5209
5210
5211
5212
5213
5214
5215
5216
5217
5218
5219
5220
5221
5222
5223
5224
5225
5226
5227
5228
5229
5230
5231
5232
5233
5234
5235
5236
5237
5238
5239
5240
5241
5242
5243
5244
5245
5246
5247
5248
5249
5250
5251
5252
5253
5254
5255
5256
5257
5258
5259
5260
5261
5262
5263
5264
5265
5266
5267
5268
5269
5270
5271
5272
5273
5274
5275
5276
5277
5278
5279
5280
5281
5282
5283
5284
5285
5286
5287
5288
5289
5290
5291
5292
5293
5294
5295
5296
5297
5298
5299
5300
5301
5302
5303
5304
5305
5306
5307
5308
5309
5310
5311
5312
5313
5314
5315
5316
5317
5318
5319
5320
5321
5322
5323
5324
5325
5326
5327
5328
5329
5330
5331
5332
5333
5334
5335
5336
5337
5338
5339
5340
5341


6783
6784
6785
6786
6787
6788
6789
6790
6791
6792
6793
6794
6795
6796
6797
6798
6799
6800
6801
6802
6803
6804
6805
6806
6807
6808
6809
6810
6811
6812
6813
6814
6815
6816
6817
6818
6819
6820
6821
6822
6823
6824
6825
6826
6827
6828
6829
6830
6831
6832
6833
6834
6835
6836
6837
6838
6839
6840
6841
6842
6843
6844
6845
6846
6847
6848
6849
6850
6851
6852
6853
6854
6855
6856
6857
6858
6859
6860
6861
6862
6863
6864
6865
6866
6867
6868
6869
6870
6871
6872
6873
6874
6875
6876
6877
6878
6879
6880
6881
6882
6883
6884
6885
6886
6887
6888
6889
6890
6891
6892
6893
6894
6895
6896
6897
6898
6899
6900
6901
6902
6903
6904
6905
6906
6907
6908
6909
6910
6911
6912
6913
6914
6915
6916
6917
6918
6919
6920
6921
6922
6923
6924
6925
6926
6927
6928
6929
6930
6931
6932
6933
6934
6935
6936
6937
6938
6939
6940
6941
6942
6943
6944
6945
6946
6947
6948
6949
6950
6951
6952
6953
6954
6955
6956
6957
6958
6959
6960
6961
6962
6963
6964
6965
6966
6967
6968
6969
6970
6971
6972
6973
6974
6975
6976
6977
6978
6979
6980
6981
6982


...

29183
29184
29185
29186
29187
29188
29189
29190
29191
29192
29193
29194
29195
29196
29197
29198
29199
29200
29201
29202
29203
29204
29205
29206
29207
29208
29209
29210
29211
29212
29213
29214
29215
29216
29217
29218
29219
29220
29221
29222
29223
29224
29225
29226
29227
29228
29229
29230
29231
29232
29233
29234
29235
29236
29237
29238
29239
29240
29241
29242
29243
29244
29245
29246
29247
29248
29249
29250
29251
29252
29253
29254
29255
29256
29257
29258
29259
29260
29261
29262
29263
29264
29265
29266
29267
29268
29269
29270
29271
29272
29273
29274
29275
29276
29277
29278
29279
29280
29281
29282
29283
29284
29285
29286
29287
29288
29289
29290
29291
29292
29293
29294
29295
29296
29297
29298
29299
29300
29301
29302
29303
29304
29305
29306
29307
29308
29309
29310
29311
29312
29313
29314
29315
29316
29317
29318
29319
29320
29321
29322
29323
29324
29325
29326
29327
29328
29329
29330
29331
29332
29333
29334
29335
29336
29337
29338
29339
29340
29341
29342
29343
29344
29345
29346
29347
29348
2934

30549
30550
30551
30552
30553
30554
30555
30556
30557
30558
30559
30560
30561
30562
30563
30564
30565
30566
30567
30568
30569
30570
30571
30572
30573
30574
30575
30576
30577
30578
30579
30580
30581
30582
30583
30584
30585
30586
30587
30588
30589
30590
30591
30592
30593
30594
30595
30596
30597
30598
30599
30600
30601
30602
30603
30604
30605
30606
30607
30608
30609
30610
30611
30612
30613
30614
30615
30616
30617
30618
30619
30620
30621
30622
30623
30624
30625
30626
30627
30628
30629
30630
30631
30632
30633
30634
30635
30636
30637
30638
30639
30640
30641
30642
30643
30644
30645
30646
30647
30648
30649
30650
30651
30652
30653
30654
30655
30656
30657
30658
30659
30660
30661
30662
30663
30664
30665
30666
30667
30668
30669
30670
30671
30672
30673
30674
30675
30676
30677
30678
30679
30680
30681
30682
30683
30684
30685
30686
30687
30688
30689
30690
30691
30692
30693
30694
30695
30696
30697
30698
30699
30700
30701
30702
30703
30704
30705
30706
30707
30708
30709
30710
30711
30712
30713
30714
3071

31916
31917
31918
31919
31920
31921
31922
31923
31924
31925
31926
31927
31928
31929
31930
31931
31932
31933
31934
31935
31936
31937
31938
31939
31940
31941
31942
31943
31944
31945
31946
31947
31948
31949
31950
31951
31952
31953
31954
31955
31956
31957
31958
31959
31960
31961
31962
31963
31964
31965
31966
31967
31968
31969
31970
31971
31972
31973
31974
31975
31976
31977
31978
31979
31980
31981
31982
31983
31984
31985
31986
31987
31988
31989
31990
31991
31992
31993
31994
31995
31996
31997
31998
31999
32000
32001
32002
32003
32004
32005
32006
32007
32008
32009
32010
32011
32012
32013
32014
32015
32016
32017
32018
32019
32020
32021
32022
32023
32024
32025
32026
32027
32028
32029
32030
32031
32032
32033
32034
32035
32036
32037
32038
32039
32040
32041
32042
32043
32044
32045
32046
32047
32048
32049
32050
32051
32052
32053
32054
32055
32056
32057
32058
32059
32060
32061
32062
32063
32064
32065
32066
32067
32068
32069
32070
32071
32072
32073
32074
32075
32076
32077
32078
32079
32080
32081
3208

33283
33284
33285
33286
33287
33288
33289
33290
33291
33292
33293
33294
33295
33296
33297
33298
33299
33300
33301
33302
33303
33304
33305
33306
33307
33308
33309
33310
33311
33312
33313
33314
33315
33316
33317
33318
33319
33320
33321
33322
33323
33324
33325
33326
33327
33328
33329
33330
33331
33332
33333
33334
33335
33336
33337
33338
33339
33340
33341
33342
33343
33344
33345
33346
33347
33348
33349
33350
33351
33352
33353
33354
33355
33356
33357
33358
33359
33360
33361
33362
33363
33364
33365
33366
33367
33368
33369
33370
33371
33372
33373
33374
33375
33376
33377
33378
33379
33380
33381
33382
33383
33384
33385
33386
33387
33388
33389
33390
33391
33392
33393
33394
33395
33396
33397
33398
33399
33400
33401
33402
33403
33404
33405
33406
33407
33408
33409
33410
33411
33412
33413
33414
33415
33416
33417
33418
33419
33420
33421
33422
33423
33424
33425
33426
33427
33428
33429
33430
33431
33432
33433
33434
33435
33436
33437
33438
33439
33440
33441
33442
33443
33444
33445
33446
33447
33448
3344

34649
34650
34651
34652
34653
34654
34655
34656
34657
34658
34659
34660
34661
34662
34663
34664
34665
34666
34667
34668
34669
34670
34671
34672
34673
34674
34675
34676
34677
34678
34679
34680
34681
34682
34683
34684
34685
34686
34687
34688
34689
34690
34691
34692
34693
34694
34695
34696
34697
34698
34699
34700
34701
34702
34703
34704
34705
34706
34707
34708
34709
34710
34711
34712
34713
34714
34715
34716
34717
34718
34719
34720
34721
34722
34723
34724
34725
34726
34727
34728
34729
34730
34731
34732
34733
34734
34735
34736
34737
34738
34739
34740
34741
34742
34743
34744
34745
34746
34747
34748
34749
34750
34751
34752
34753
34754
34755
34756
34757
34758
34759
34760
34761
34762
34763
34764
34765
34766
34767
34768
34769
34770
34771
34772
34773
34774
34775
34776
34777
34778
34779
34780
34781
34782
34783
34784
34785
34786
34787
34788
34789
34790
34791
34792
34793
34794
34795
34796
34797
34798
34799
34800
34801
34802
34803
34804
34805
34806
34807
34808
34809
34810
34811
34812
34813
34814
3481

In [13]:
# Finding Expception Waveforms

exceptions_waveforms = []
wvDF_array_new = []

for i in range(len(wvDF_array)):
    
    beam_new = []
    
    for j in range(len(wvDF_array[i])):
        
        df_spline = wvDF_array[i][j]
        y = df_spline['Elevation (m)']
        x = df_spline['Amplitude (DN)']
        x_new = df_spline['Amplitude (DN)']
        
        try:
            f_new = interp1d(x, y, kind='cubic')
            beam_new.append(df_spline)  
        except:
            arr = []
            arr.append(i)
            arr.append(j)
            arr.append(df_spline)
            exceptions_waveforms.append(arr)
        
            print("Beam Index:", i, " ", "Shot Index:", j)
        
    wvDF_array_new.append(beam_new)

Beam Index: 0   Shot Index: 1
Beam Index: 0   Shot Index: 42
Beam Index: 0   Shot Index: 69
Beam Index: 0   Shot Index: 278
Beam Index: 0   Shot Index: 281
Beam Index: 0   Shot Index: 282
Beam Index: 0   Shot Index: 283
Beam Index: 0   Shot Index: 285
Beam Index: 0   Shot Index: 286
Beam Index: 0   Shot Index: 287
Beam Index: 0   Shot Index: 288
Beam Index: 0   Shot Index: 289
Beam Index: 0   Shot Index: 290
Beam Index: 0   Shot Index: 292
Beam Index: 0   Shot Index: 295
Beam Index: 0   Shot Index: 298
Beam Index: 0   Shot Index: 299
Beam Index: 0   Shot Index: 300
Beam Index: 0   Shot Index: 301
Beam Index: 0   Shot Index: 303
Beam Index: 0   Shot Index: 304
Beam Index: 0   Shot Index: 308
Beam Index: 0   Shot Index: 310
Beam Index: 0   Shot Index: 312
Beam Index: 0   Shot Index: 313
Beam Index: 0   Shot Index: 314
Beam Index: 0   Shot Index: 316
Beam Index: 0   Shot Index: 318
Beam Index: 0   Shot Index: 319
Beam Index: 0   Shot Index: 323
Beam Index: 0   Shot Index: 324
Beam Index: 

Beam Index: 0   Shot Index: 1078
Beam Index: 0   Shot Index: 1079
Beam Index: 0   Shot Index: 1082
Beam Index: 0   Shot Index: 1083
Beam Index: 0   Shot Index: 1084
Beam Index: 0   Shot Index: 1088
Beam Index: 0   Shot Index: 1094
Beam Index: 0   Shot Index: 1098
Beam Index: 0   Shot Index: 1101
Beam Index: 0   Shot Index: 1102
Beam Index: 0   Shot Index: 1107
Beam Index: 0   Shot Index: 1113
Beam Index: 0   Shot Index: 1116
Beam Index: 0   Shot Index: 1118
Beam Index: 0   Shot Index: 1120
Beam Index: 0   Shot Index: 1126
Beam Index: 0   Shot Index: 1140
Beam Index: 0   Shot Index: 1144
Beam Index: 0   Shot Index: 1153
Beam Index: 0   Shot Index: 1155
Beam Index: 0   Shot Index: 1158
Beam Index: 0   Shot Index: 1167
Beam Index: 0   Shot Index: 1171
Beam Index: 0   Shot Index: 1172
Beam Index: 0   Shot Index: 1178
Beam Index: 0   Shot Index: 1181
Beam Index: 0   Shot Index: 1182
Beam Index: 0   Shot Index: 1184
Beam Index: 0   Shot Index: 1186
Beam Index: 0   Shot Index: 1188
Beam Index

Beam Index: 0   Shot Index: 1825
Beam Index: 0   Shot Index: 1828
Beam Index: 0   Shot Index: 1829
Beam Index: 0   Shot Index: 1830
Beam Index: 0   Shot Index: 1834
Beam Index: 0   Shot Index: 1837
Beam Index: 0   Shot Index: 1838
Beam Index: 0   Shot Index: 1841
Beam Index: 0   Shot Index: 1846
Beam Index: 0   Shot Index: 1848
Beam Index: 0   Shot Index: 1850
Beam Index: 0   Shot Index: 1852
Beam Index: 0   Shot Index: 1854
Beam Index: 0   Shot Index: 1856
Beam Index: 0   Shot Index: 1857
Beam Index: 0   Shot Index: 1859
Beam Index: 0   Shot Index: 1860
Beam Index: 0   Shot Index: 1863
Beam Index: 0   Shot Index: 1866
Beam Index: 0   Shot Index: 1924
Beam Index: 0   Shot Index: 1945
Beam Index: 0   Shot Index: 1947
Beam Index: 0   Shot Index: 2060
Beam Index: 0   Shot Index: 2110
Beam Index: 0   Shot Index: 2147
Beam Index: 0   Shot Index: 2148
Beam Index: 0   Shot Index: 2149
Beam Index: 0   Shot Index: 2153
Beam Index: 0   Shot Index: 2156
Beam Index: 0   Shot Index: 2160
Beam Index

Beam Index: 0   Shot Index: 2669
Beam Index: 0   Shot Index: 2670
Beam Index: 0   Shot Index: 2671
Beam Index: 0   Shot Index: 2673
Beam Index: 0   Shot Index: 2674
Beam Index: 0   Shot Index: 2676
Beam Index: 0   Shot Index: 2680
Beam Index: 0   Shot Index: 2681
Beam Index: 0   Shot Index: 2683
Beam Index: 0   Shot Index: 2686
Beam Index: 0   Shot Index: 2689
Beam Index: 0   Shot Index: 2692
Beam Index: 0   Shot Index: 2694
Beam Index: 0   Shot Index: 2695
Beam Index: 0   Shot Index: 2696
Beam Index: 0   Shot Index: 2701
Beam Index: 0   Shot Index: 2702
Beam Index: 0   Shot Index: 2704
Beam Index: 0   Shot Index: 2707
Beam Index: 0   Shot Index: 2708
Beam Index: 0   Shot Index: 2710
Beam Index: 0   Shot Index: 2713
Beam Index: 0   Shot Index: 2715
Beam Index: 0   Shot Index: 2718
Beam Index: 0   Shot Index: 2719
Beam Index: 0   Shot Index: 2720
Beam Index: 0   Shot Index: 2723
Beam Index: 0   Shot Index: 2725
Beam Index: 0   Shot Index: 2726
Beam Index: 0   Shot Index: 2727
Beam Index

Beam Index: 0   Shot Index: 3117
Beam Index: 0   Shot Index: 3118
Beam Index: 0   Shot Index: 3120
Beam Index: 0   Shot Index: 3121
Beam Index: 0   Shot Index: 3123
Beam Index: 0   Shot Index: 3124
Beam Index: 0   Shot Index: 3125
Beam Index: 0   Shot Index: 3127
Beam Index: 0   Shot Index: 3129
Beam Index: 0   Shot Index: 3130
Beam Index: 0   Shot Index: 3131
Beam Index: 0   Shot Index: 3133
Beam Index: 0   Shot Index: 3135
Beam Index: 0   Shot Index: 3136
Beam Index: 0   Shot Index: 3138
Beam Index: 0   Shot Index: 3141
Beam Index: 0   Shot Index: 3142
Beam Index: 0   Shot Index: 3143
Beam Index: 0   Shot Index: 3144
Beam Index: 0   Shot Index: 3147
Beam Index: 0   Shot Index: 3148
Beam Index: 0   Shot Index: 3149
Beam Index: 0   Shot Index: 3150
Beam Index: 0   Shot Index: 3151
Beam Index: 0   Shot Index: 3152
Beam Index: 0   Shot Index: 3153
Beam Index: 0   Shot Index: 3155
Beam Index: 0   Shot Index: 3156
Beam Index: 0   Shot Index: 3160
Beam Index: 0   Shot Index: 3161
Beam Index

...

Beam Index: 7   Shot Index: 564
Beam Index: 7   Shot Index: 730
Beam Index: 7   Shot Index: 733
Beam Index: 7   Shot Index: 738
Beam Index: 7   Shot Index: 739
Beam Index: 7   Shot Index: 743
Beam Index: 7   Shot Index: 745
Beam Index: 7   Shot Index: 746
Beam Index: 7   Shot Index: 747
Beam Index: 7   Shot Index: 749
Beam Index: 7   Shot Index: 750
Beam Index: 7   Shot Index: 752
Beam Index: 7   Shot Index: 753
Beam Index: 7   Shot Index: 754
Beam Index: 7   Shot Index: 757
Beam Index: 7   Shot Index: 758
Beam Index: 7   Shot Index: 762
Beam Index: 7   Shot Index: 763
Beam Index: 7   Shot Index: 764
Beam Index: 7   Shot Index: 765
Beam Index: 7   Shot Index: 767
Beam Index: 7   Shot Index: 769
Beam Index: 7   Shot Index: 772
Beam Index: 7   Shot Index: 776
Beam Index: 7   Shot Index: 777
Beam Index: 7   Shot Index: 778
Beam Index: 7   Shot Index: 780
Beam Index: 7   Shot Index: 781
Beam Index: 7   Shot Index: 784
Beam Index: 7   Shot Index: 785
Beam Index: 7   Shot Index: 787
Beam Ind

Beam Index: 7   Shot Index: 1451
Beam Index: 7   Shot Index: 1452
Beam Index: 7   Shot Index: 1453
Beam Index: 7   Shot Index: 1454
Beam Index: 7   Shot Index: 1456
Beam Index: 7   Shot Index: 1457
Beam Index: 7   Shot Index: 1458
Beam Index: 7   Shot Index: 1459
Beam Index: 7   Shot Index: 1460
Beam Index: 7   Shot Index: 1465
Beam Index: 7   Shot Index: 1468
Beam Index: 7   Shot Index: 1469
Beam Index: 7   Shot Index: 1471
Beam Index: 7   Shot Index: 1472
Beam Index: 7   Shot Index: 1476
Beam Index: 7   Shot Index: 1477
Beam Index: 7   Shot Index: 1480
Beam Index: 7   Shot Index: 1482
Beam Index: 7   Shot Index: 1484
Beam Index: 7   Shot Index: 1486
Beam Index: 7   Shot Index: 1488
Beam Index: 7   Shot Index: 1492
Beam Index: 7   Shot Index: 1494
Beam Index: 7   Shot Index: 1497
Beam Index: 7   Shot Index: 1498
Beam Index: 7   Shot Index: 1500
Beam Index: 7   Shot Index: 1501
Beam Index: 7   Shot Index: 1503
Beam Index: 7   Shot Index: 1504
Beam Index: 7   Shot Index: 1508
Beam Index

Beam Index: 7   Shot Index: 2247
Beam Index: 7   Shot Index: 2248
Beam Index: 7   Shot Index: 2253
Beam Index: 7   Shot Index: 2254
Beam Index: 7   Shot Index: 2257
Beam Index: 7   Shot Index: 2263
Beam Index: 7   Shot Index: 2267
Beam Index: 7   Shot Index: 2269
Beam Index: 7   Shot Index: 2271
Beam Index: 7   Shot Index: 2275
Beam Index: 7   Shot Index: 2277
Beam Index: 7   Shot Index: 2278
Beam Index: 7   Shot Index: 2280
Beam Index: 7   Shot Index: 2282
Beam Index: 7   Shot Index: 2284
Beam Index: 7   Shot Index: 2285
Beam Index: 7   Shot Index: 2291
Beam Index: 7   Shot Index: 2292
Beam Index: 7   Shot Index: 2297
Beam Index: 7   Shot Index: 2301
Beam Index: 7   Shot Index: 2302
Beam Index: 7   Shot Index: 2306
Beam Index: 7   Shot Index: 2308
Beam Index: 7   Shot Index: 2317
Beam Index: 7   Shot Index: 2319
Beam Index: 7   Shot Index: 2324
Beam Index: 7   Shot Index: 2325
Beam Index: 7   Shot Index: 2329
Beam Index: 7   Shot Index: 2330
Beam Index: 7   Shot Index: 2331
Beam Index

Beam Index: 7   Shot Index: 2889
Beam Index: 7   Shot Index: 2894
Beam Index: 7   Shot Index: 2896
Beam Index: 7   Shot Index: 2899
Beam Index: 7   Shot Index: 2902
Beam Index: 7   Shot Index: 2903
Beam Index: 7   Shot Index: 2904
Beam Index: 7   Shot Index: 2905
Beam Index: 7   Shot Index: 2906
Beam Index: 7   Shot Index: 2907
Beam Index: 7   Shot Index: 2909
Beam Index: 7   Shot Index: 2910
Beam Index: 7   Shot Index: 2911
Beam Index: 7   Shot Index: 2913
Beam Index: 7   Shot Index: 2914
Beam Index: 7   Shot Index: 2916
Beam Index: 7   Shot Index: 2917
Beam Index: 7   Shot Index: 2918
Beam Index: 7   Shot Index: 2919
Beam Index: 7   Shot Index: 2921
Beam Index: 7   Shot Index: 2922
Beam Index: 7   Shot Index: 2923
Beam Index: 7   Shot Index: 2924
Beam Index: 7   Shot Index: 2926
Beam Index: 7   Shot Index: 2928
Beam Index: 7   Shot Index: 2931
Beam Index: 7   Shot Index: 2933
Beam Index: 7   Shot Index: 2937
Beam Index: 7   Shot Index: 2939
Beam Index: 7   Shot Index: 2940
Beam Index

Beam Index: 7   Shot Index: 3376
Beam Index: 7   Shot Index: 3382
Beam Index: 7   Shot Index: 3392
Beam Index: 7   Shot Index: 3393
Beam Index: 7   Shot Index: 3395
Beam Index: 7   Shot Index: 3410
Beam Index: 7   Shot Index: 3418
Beam Index: 7   Shot Index: 3424
Beam Index: 7   Shot Index: 3427
Beam Index: 7   Shot Index: 3432
Beam Index: 7   Shot Index: 3440
Beam Index: 7   Shot Index: 3443
Beam Index: 7   Shot Index: 3444
Beam Index: 7   Shot Index: 3446
Beam Index: 7   Shot Index: 3448
Beam Index: 7   Shot Index: 3450
Beam Index: 7   Shot Index: 3451
Beam Index: 7   Shot Index: 3452
Beam Index: 7   Shot Index: 3453
Beam Index: 7   Shot Index: 3456
Beam Index: 7   Shot Index: 3457
Beam Index: 7   Shot Index: 3459
Beam Index: 7   Shot Index: 3460
Beam Index: 7   Shot Index: 3462
Beam Index: 7   Shot Index: 3463
Beam Index: 7   Shot Index: 3464
Beam Index: 7   Shot Index: 3465
Beam Index: 7   Shot Index: 3467
Beam Index: 7   Shot Index: 3468
Beam Index: 7   Shot Index: 3469
Beam Index

In [14]:
wvDF_array = wvDF_array_new

In [15]:
t = 0

for i in range(len(wvDF_array)):
    t += len(wvDF_array[i])
    print("total shots in beam index ", i, " ", len(wvDF_array[i]))

print("\ntotal shots without exception waveforms: ", t)
print("\ntotal shots with exception waveforms: ", t + len(exceptions_waveforms))

total shots in beam index  0   2247
total shots in beam index  1   2171
total shots in beam index  2   2107
total shots in beam index  3   2062
total shots in beam index  4   2312
total shots in beam index  5   8367
total shots in beam index  6   2236
total shots in beam index  7   2178

total shots without exception waveforms:  23680

total shots with exception waveforms:  35472


In [18]:
process = psutil.Process(os.getpid())

In [19]:
process

psutil.Process(pid=11776, name='python.exe', status='running', started='20:08:47')

In [20]:
# COMPUTER USAGE FOR 1D INTERPOLATION

computer_usage_1d = []
interpolation = []
overall_ram_1d = 0.0

ram_start_1d = process.memory_info().rss

for i in range(len(wvDF_array)):
    interpolation_beam = []
    beam_compute_usage = []
    for j in range(len(wvDF_array[i])):
        shot_compute_usage = []
    
        df_spline = wvDF_array[i][j]
        y = df_spline['Elevation (m)']
        x = df_spline['Amplitude (DN)']
        
        
        total_time = 0.0
        total_ram = 0.0
        
        f = interp1d(x, y)
        no_times = 50
        
        for k in range(no_times):
            ram_start = process.memory_info().rss
            start = time.time() 
            
            f(x)

            end = time.time()
            ram_end = process.memory_info().rss
            
            
            total_time += (end - start)
            total_ram += (ram_end - ram_start)
            
            
        interpolation_beam.append(f(x))

        avg_time = total_time / no_times
        avg_ram = total_ram / no_times
        
        shot_compute_usage.append(avg_time)
        shot_compute_usage.append(avg_ram)
    
        
        beam_compute_usage.append(shot_compute_usage)
        
        print("Beam Index:", i, " ", "Shot Index:", j, " ", "Time Taken:", avg_time, " ", " RAM used: ", avg_ram)
        
    computer_usage_1d.append(beam_compute_usage)
    interpolation.append(interpolation_beam)

ram_end_1d = process.memory_info().rss

overall_ram_1d = ram_end_1d - ram_start_1d

Beam Index: 0   Shot Index: 0   Time Taken: 0.00019992828369140624    RAM used:  983.04
Beam Index: 0   Shot Index: 1   Time Taken: 0.00018013477325439452    RAM used:  0.0
Beam Index: 0   Shot Index: 2   Time Taken: 0.00017990589141845704    RAM used:  0.0
Beam Index: 0   Shot Index: 3   Time Taken: 0.00019989490509033202    RAM used:  0.0
Beam Index: 0   Shot Index: 4   Time Taken: 0.00019990921020507813    RAM used:  0.0
Beam Index: 0   Shot Index: 5   Time Taken: 0.0004044961929321289    RAM used:  0.0
Beam Index: 0   Shot Index: 6   Time Taken: 0.00035740375518798827    RAM used:  0.0
Beam Index: 0   Shot Index: 7   Time Taken: 0.0    RAM used:  0.0
Beam Index: 0   Shot Index: 8   Time Taken: 0.00031259059906005857    RAM used:  0.0
Beam Index: 0   Shot Index: 9   Time Taken: 0.00031257152557373046    RAM used:  0.0
Beam Index: 0   Shot Index: 10   Time Taken: 0.0003124237060546875    RAM used:  0.0
Beam Index: 0   Shot Index: 11   Time Taken: 0.00031239986419677733    RAM used:  

Beam Index: 0   Shot Index: 106   Time Taken: 0.00012842178344726562    RAM used:  0.0
Beam Index: 0   Shot Index: 107   Time Taken: 0.0005372047424316406    RAM used:  0.0
Beam Index: 0   Shot Index: 108   Time Taken: 0.00025997161865234377    RAM used:  0.0
Beam Index: 0   Shot Index: 109   Time Taken: 0.0004600191116333008    RAM used:  0.0
Beam Index: 0   Shot Index: 110   Time Taken: 0.00047449111938476564    RAM used:  0.0
Beam Index: 0   Shot Index: 111   Time Taken: 0.0006247234344482422    RAM used:  0.0
Beam Index: 0   Shot Index: 112   Time Taken: 0.00031244277954101563    RAM used:  0.0
Beam Index: 0   Shot Index: 113   Time Taken: 0.00029985904693603517    RAM used:  0.0
Beam Index: 0   Shot Index: 114   Time Taken: 0.00039978981018066404    RAM used:  0.0
Beam Index: 0   Shot Index: 115   Time Taken: 0.0002998065948486328    RAM used:  0.0
Beam Index: 0   Shot Index: 116   Time Taken: 0.00020077705383300781    RAM used:  0.0
Beam Index: 0   Shot Index: 117   Time Taken: 0

Beam Index: 0   Shot Index: 207   Time Taken: 0.00023986339569091796    RAM used:  0.0
Beam Index: 0   Shot Index: 208   Time Taken: 0.0004397726058959961    RAM used:  0.0
Beam Index: 0   Shot Index: 209   Time Taken: 0.00041999340057373045    RAM used:  0.0
Beam Index: 0   Shot Index: 210   Time Taken: 0.00021984100341796876    RAM used:  0.0
Beam Index: 0   Shot Index: 211   Time Taken: 0.00020017147064208985    RAM used:  0.0
Beam Index: 0   Shot Index: 212   Time Taken: 0.00037971973419189455    RAM used:  0.0
Beam Index: 0   Shot Index: 213   Time Taken: 0.00044048309326171875    RAM used:  0.0
Beam Index: 0   Shot Index: 214   Time Taken: 0.0005397319793701172    RAM used:  0.0
Beam Index: 0   Shot Index: 215   Time Taken: 0.00035986900329589846    RAM used:  0.0
Beam Index: 0   Shot Index: 216   Time Taken: 0.00027910232543945315    RAM used:  0.0
Beam Index: 0   Shot Index: 217   Time Taken: 0.00023993492126464844    RAM used:  0.0
Beam Index: 0   Shot Index: 218   Time Taken:

Beam Index: 0   Shot Index: 306   Time Taken: 0.00029985904693603517    RAM used:  0.0
Beam Index: 0   Shot Index: 307   Time Taken: 0.0002998495101928711    RAM used:  0.0
Beam Index: 0   Shot Index: 308   Time Taken: 0.0005597114562988281    RAM used:  0.0
Beam Index: 0   Shot Index: 309   Time Taken: 0.000379786491394043    RAM used:  0.0
Beam Index: 0   Shot Index: 310   Time Taken: 0.0006995820999145508    RAM used:  0.0
Beam Index: 0   Shot Index: 311   Time Taken: 0.00030005931854248046    RAM used:  0.0
Beam Index: 0   Shot Index: 312   Time Taken: 0.0006947994232177734    RAM used:  0.0
Beam Index: 0   Shot Index: 313   Time Taken: 0.0007033014297485352    RAM used:  0.0
Beam Index: 0   Shot Index: 314   Time Taken: 0.0005190896987915039    RAM used:  0.0
Beam Index: 0   Shot Index: 315   Time Taken: 0.0005000877380371094    RAM used:  0.0
Beam Index: 0   Shot Index: 316   Time Taken: 0.0003399944305419922    RAM used:  0.0
Beam Index: 0   Shot Index: 317   Time Taken: 0.00059

Beam Index: 0   Shot Index: 415   Time Taken: 0.0001799154281616211    RAM used:  0.0
Beam Index: 0   Shot Index: 416   Time Taken: 0.00021079063415527344    RAM used:  0.0
Beam Index: 0   Shot Index: 417   Time Taken: 0.00017990589141845704    RAM used:  0.0
Beam Index: 0   Shot Index: 418   Time Taken: 0.00013992786407470703    RAM used:  0.0
Beam Index: 0   Shot Index: 419   Time Taken: 0.00019988536834716797    RAM used:  0.0
Beam Index: 0   Shot Index: 420   Time Taken: 0.0001799154281616211    RAM used:  0.0
Beam Index: 0   Shot Index: 421   Time Taken: 0.00017992019653320312    RAM used:  0.0
Beam Index: 0   Shot Index: 422   Time Taken: 5.4640769958496095e-05    RAM used:  0.0
Beam Index: 0   Shot Index: 423   Time Taken: 0.0    RAM used:  0.0
Beam Index: 0   Shot Index: 424   Time Taken: 0.00031249046325683595    RAM used:  0.0
Beam Index: 0   Shot Index: 425   Time Taken: 0.0    RAM used:  0.0
Beam Index: 0   Shot Index: 426   Time Taken: 0.0003124856948852539    RAM used:  0

...

Beam Index: 7   Shot Index: 1729   Time Taken: 0.000339813232421875    RAM used:  163.84
Beam Index: 7   Shot Index: 1730   Time Taken: 0.0002598714828491211    RAM used:  0.0
Beam Index: 7   Shot Index: 1731   Time Taken: 0.00029988765716552733    RAM used:  0.0
Beam Index: 7   Shot Index: 1732   Time Taken: 0.00027987003326416013    RAM used:  0.0
Beam Index: 7   Shot Index: 1733   Time Taken: 0.0001599407196044922    RAM used:  0.0
Beam Index: 7   Shot Index: 1734   Time Taken: 0.00025986671447753907    RAM used:  0.0
Beam Index: 7   Shot Index: 1735   Time Taken: 0.000399932861328125    RAM used:  1392.64
Beam Index: 7   Shot Index: 1736   Time Taken: 0.0002598905563354492    RAM used:  81.92
Beam Index: 7   Shot Index: 1737   Time Taken: 0.00023988723754882812    RAM used:  81.92
Beam Index: 7   Shot Index: 1738   Time Taken: 0.0002399158477783203    RAM used:  81.92
Beam Index: 7   Shot Index: 1739   Time Taken: 0.0004796504974365234    RAM used:  0.0
Beam Index: 7   Shot Index: 

Beam Index: 7   Shot Index: 1831   Time Taken: 0.0003994417190551758    RAM used:  0.0
Beam Index: 7   Shot Index: 1832   Time Taken: 0.0005797004699707031    RAM used:  245.76
Beam Index: 7   Shot Index: 1833   Time Taken: 0.00029979705810546876    RAM used:  0.0
Beam Index: 7   Shot Index: 1834   Time Taken: 0.0002998638153076172    RAM used:  81.92
Beam Index: 7   Shot Index: 1835   Time Taken: 0.00025988101959228515    RAM used:  0.0
Beam Index: 7   Shot Index: 1836   Time Taken: 0.00037975311279296874    RAM used:  0.0
Beam Index: 7   Shot Index: 1837   Time Taken: 0.0002997827529907227    RAM used:  0.0
Beam Index: 7   Shot Index: 1838   Time Taken: 0.00025984764099121096    RAM used:  81.92
Beam Index: 7   Shot Index: 1839   Time Taken: 0.00023989200592041014    RAM used:  0.0
Beam Index: 7   Shot Index: 1840   Time Taken: 0.0002399158477783203    RAM used:  0.0
Beam Index: 7   Shot Index: 1841   Time Taken: 0.00025988101959228515    RAM used:  0.0
Beam Index: 7   Shot Index: 18

Beam Index: 7   Shot Index: 1925   Time Taken: 0.00023993492126464844    RAM used:  163.84
Beam Index: 7   Shot Index: 1926   Time Taken: 0.00031983375549316407    RAM used:  0.0
Beam Index: 7   Shot Index: 1927   Time Taken: 0.00029985427856445314    RAM used:  0.0
Beam Index: 7   Shot Index: 1928   Time Taken: 0.00043980598449707033    RAM used:  0.0
Beam Index: 7   Shot Index: 1929   Time Taken: 0.00039979934692382815    RAM used:  81.92
Beam Index: 7   Shot Index: 1930   Time Taken: 0.0004797077178955078    RAM used:  0.0
Beam Index: 7   Shot Index: 1931   Time Taken: 0.00029981136322021484    RAM used:  0.0
Beam Index: 7   Shot Index: 1932   Time Taken: 0.0002998447418212891    RAM used:  0.0
Beam Index: 7   Shot Index: 1933   Time Taken: 0.0005795907974243164    RAM used:  0.0
Beam Index: 7   Shot Index: 1934   Time Taken: 0.00035982131958007814    RAM used:  0.0
Beam Index: 7   Shot Index: 1935   Time Taken: 0.0006402969360351562    RAM used:  0.0
Beam Index: 7   Shot Index: 193

Beam Index: 7   Shot Index: 2019   Time Taken: 0.0003397941589355469    RAM used:  0.0
Beam Index: 7   Shot Index: 2020   Time Taken: 0.0002599143981933594    RAM used:  81.92
Beam Index: 7   Shot Index: 2021   Time Taken: 0.000259852409362793    RAM used:  81.92
Beam Index: 7   Shot Index: 2022   Time Taken: 0.00021993160247802735    RAM used:  327.68
Beam Index: 7   Shot Index: 2023   Time Taken: 0.00035985946655273435    RAM used:  0.0
Beam Index: 7   Shot Index: 2024   Time Taken: 0.0002799844741821289    RAM used:  163.84
Beam Index: 7   Shot Index: 2025   Time Taken: 0.0002398538589477539    RAM used:  0.0
Beam Index: 7   Shot Index: 2026   Time Taken: 0.0002598857879638672    RAM used:  0.0
Beam Index: 7   Shot Index: 2027   Time Taken: 0.0003198385238647461    RAM used:  0.0
Beam Index: 7   Shot Index: 2028   Time Taken: 0.0002798652648925781    RAM used:  0.0
Beam Index: 7   Shot Index: 2029   Time Taken: 0.0003801393508911133    RAM used:  0.0
Beam Index: 7   Shot Index: 2030

Beam Index: 7   Shot Index: 2118   Time Taken: 0.00027984142303466797    RAM used:  0.0
Beam Index: 7   Shot Index: 2119   Time Taken: 0.00023990631103515625    RAM used:  0.0
Beam Index: 7   Shot Index: 2120   Time Taken: 0.00023991107940673828    RAM used:  0.0
Beam Index: 7   Shot Index: 2121   Time Taken: 0.0004599142074584961    RAM used:  0.0
Beam Index: 7   Shot Index: 2122   Time Taken: 0.00021988391876220703    RAM used:  163.84
Beam Index: 7   Shot Index: 2123   Time Taken: 0.0001992654800415039    RAM used:  81.92
Beam Index: 7   Shot Index: 2124   Time Taken: 0.00027987003326416013    RAM used:  0.0
Beam Index: 7   Shot Index: 2125   Time Taken: 0.00029967308044433595    RAM used:  0.0
Beam Index: 7   Shot Index: 2126   Time Taken: 0.00025988101959228515    RAM used:  0.0
Beam Index: 7   Shot Index: 2127   Time Taken: 0.0002798652648925781    RAM used:  81.92
Beam Index: 7   Shot Index: 2128   Time Taken: 0.0002598905563354492    RAM used:  0.0
Beam Index: 7   Shot Index: 2

In [21]:
overall_ram_1d

98074624

In [22]:
r_squared_array = []
sum_rsq = 0.0
for i in range(len(interpolation)): # beam loop
    r_squared_array_beam = []
    
    for j in range(len(interpolation[i])): # shot loop
        r_squared = 0.0
        df_spline = wvDF_array[i][j]
        y = df_spline['Elevation (m)']
        
        for k in range(len(interpolation[i][j])): # each of 101 points in the shot
            r_squared += pow((interpolation[i][j][k] - y[k]), 2)
        
        sum_rsq += r_squared
        print(sum_rsq)
            
        r_squared_array_beam.append(r_squared)
        
    r_squared_array.append(r_squared_array_beam)

0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
0.0
1.262177448353619e-29
6.310887241768094e-29
6.310887241768094e-29
7.573064690121713e-29
7.573064690121713e-29
7.573064690121713e-29
7.573064690121713e-29
8.835242138475332e-29
1.0097419586828951e-28
1.262177448353619e-28
1.3883951931889808e-28
1.3883951931889808e-28
1.3883951931889808e-28
1.7670484276950664e-28
1.8932661725304283e-28
1.8932661725304283e-28
2.145701662201152e-28
2.271919407036514e-28
2.524354896707238e-28
2.524354896707238e-28
2.524354896707238e-28
2.6505726415425997e-28
2.9030081312133234e-28
3.0292258760486853e-28
3.0292258760486853e-28
3.0292258760486853e-28
3.0292258760486853e-28
3.155443620884047e-28
3.407879110554771e-28
3.407879110554771e-28
3.407879110554771e-28
3.407879110554771e-28
3.4394335467636115e-28
3.4394335467636115e-28
3.4394335467636115e-28
3.4394335467636115e-28
3.4394335467636115e-28
3.4394335467636115e-28
3.5656512915989734e-28
3.5656512915989734e-28
3.5656512915989734e-28
3.5656512915989734e-28
3.565651291598973

3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.7728208948222257e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25
3.773199548056732e-25


4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492889e-25
4.85879245492

8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.011272423999635e-25
8.01127242

9.364495514172239e-25
9.416662885834504e-25
9.465319826468536e-25
9.538155353847592e-25
9.610352396931485e-25
9.680284916179328e-25
1.0028992990723224e-24
1.0090839685692551e-24
1.0139994101734938e-24
1.019702134961143e-24
1.0259248669967527e-24
1.0307148304132547e-24
1.036681823604153e-24
1.0417906840415906e-24
1.0478002264175643e-24
1.052613264015544e-24
1.0591402991453426e-24
1.0648066870275451e-24
1.0700399902727813e-24
1.0761489291228128e-24
1.080507385624159e-24
1.0862337269351583e-24
1.0933374193866735e-24
1.0992586093412624e-24
1.1064443433269206e-24
1.111944330861928e-24
1.1170096067343522e-24
1.122591586499696e-24
1.1286421496427412e-24
1.1360676973435866e-24
1.1434159366757203e-24
1.1522456567878591e-24
1.1593114839159237e-24
1.1661682629041047e-24
1.1709836670848001e-24
1.1761562280403343e-24
1.1832086445330101e-24
1.1897041252266e-24
1.1943678708982666e-24
1.2006700806700772e-24
1.206697175201192e-24
1.2128881555853666e-24
1.219240901758918e-24
1.2247881716444321e-24
1.230

...

1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.6243260754509167e-23
1.624326075

1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.637533500270489e-23
1.63753350

1.64500317487822e-23
1.64500317487822e-23
1.64500317487822e-23
1.6450044370556685e-23
1.6450082235880135e-23
1.645009485765462e-23
1.645009485765462e-23
1.645009485765462e-23
1.6450107479429102e-23
1.645013272297807e-23
1.6450145344752553e-23
1.6450157966527037e-23
1.645017058830152e-23
1.6450195831850487e-23
1.6450195831850487e-23
1.6450221075399454e-23
1.6450221075399454e-23
1.6450233697173938e-23
1.645024631894842e-23
1.6450258940722905e-23
1.6450284184271872e-23
1.6450284184271872e-23
1.6450284184271872e-23
1.6450284184271872e-23
1.6450296806046355e-23
1.6450296806046355e-23
1.645030942782084e-23
1.6450322049595323e-23
1.645034729314429e-23
1.645668263507412e-23
1.6463402990429504e-23
1.6468109729020505e-23
1.6474266196740076e-23
1.648026232848066e-23
1.6485591872756334e-23
1.6485591872756334e-23
1.64926089877235e-23
1.649910289069528e-23
1.6505309845512786e-23
1.6512129745253648e-23
1.6512129745253648e-23
1.6517128756810034e-23
1.652393031553485e-23
1.6528799953902778e-23
1.653515

1.7172560311037524e-23
1.7177526979296796e-23
1.7183342461890085e-23
1.718837401395881e-23
1.7192268028602208e-23
1.7196856043626974e-23
1.720283876473217e-23
1.7207322650117446e-23
1.7211848542345925e-23
1.7217070998753715e-23
1.7217070998753715e-23
1.7223508892601223e-23
1.7229599687650435e-23
1.7236387046878956e-23
1.7242391067228594e-23
1.724713389620601e-23
1.7251558863542426e-23
1.7256715647279856e-23
1.7261949147740318e-23
1.7266997857533733e-23
1.7271033669924844e-23
1.727663463165572e-23
1.7281608399663138e-23
1.7286184581774325e-23
1.7291683533929394e-23
1.7297957394012423e-23
1.7303318492724305e-23
1.7309107351262044e-23
1.7314103404590035e-23
1.7319257032883843e-23
1.732446035941468e-23
1.7330553521046608e-23
1.733718943130728e-23
1.734245981101506e-23
1.734706044781431e-23
1.7351493846101652e-23
1.7356199795831748e-23
1.7361803863702438e-23
1.736855966849475e-23
1.7373750767681557e-23
1.737786314888428e-23
1.7382805559670717e-23
1.738777853881723e-23
1.739213620645767e-23


1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23
1.7904975090779743e-23


In [23]:
sum1 = 0.0
for i in range(len(r_squared_array)):
    for j in range(len(r_squared_array[i])):
        sum1 += r_squared_array[i][j]

print("CALCULATION METHOD 1: Linear Interpolation total r-squared value: ", sum_rsq)
print("CALCULATION METHOD 1: Linear Interpolation average r-squared value: ", sum_rsq / t)

print("CALCULATION METHOD 2: Linear Interpolation total r-squared value: ", sum1)
print("CALCULATION METHOD 2: Linear Interpolation average r-squared value: ", sum1 / t)

CALCULATION METHOD 1: Linear Interpolation total r-squared value:  1.7904975090779743e-23
CALCULATION METHOD 1: Linear Interpolation average r-squared value:  7.561222589011715e-28
CALCULATION METHOD 2: Linear Interpolation total r-squared value:  1.7904975090779743e-23
CALCULATION METHOD 2: Linear Interpolation average r-squared value:  7.561222589011715e-28


In [24]:
# COMPUTER USAGE FOR CUBIC INTERPOLATION

computer_usage_cubic = []
interpolation_cubic = []
overall_ram_cubic = 0.0

ram_start_cubic = process.memory_info().rss

for i in range(len(wvDF_array)):
    beam_compute_usage = []
    interpolation_beam_cubic = []
    
    for j in range(len(wvDF_array[i])):
        shot_compute_usage = []
        
        df_spline = wvDF_array[i][j]
        y = df_spline['Elevation (m)']
        x = df_spline['Amplitude (DN)']
        x_new = df_spline['Amplitude (DN)']
        
        
        total_time = 0
        total_ram = 0.0
        no_times = 50
        
        f_new = interp1d(x, y, kind='cubic')
            
        for k in range(no_times):
            ram_start = process.memory_info().rss
            start = time.time()

            f_new(x_new)

            end = time.time()
            ram_end = process.memory_info().rss
            
            total_time += (end - start)
            total_ram += (ram_end - ram_start)
            
        avg_time = total_time / no_times
        avg_ram = total_ram / no_times
        
        shot_compute_usage.append(avg_time)
        shot_compute_usage.append(avg_ram)
        
        interpolation_beam_cubic.append(f_new(x))
        beam_compute_usage.append(shot_compute_usage)
        
        print("Beam Index:", i, " ", "Shot Index:", j, " ", "Time Taken:", avg_time, " ", " RAM used: ", avg_ram)
        
    computer_usage_cubic.append(beam_compute_usage)
    interpolation_cubic.append(interpolation_beam_cubic)

ram_end_cubic = process.memory_info().rss
overall_ram_cubic = ram_end_cubic - ram_start_cubic

Beam Index: 0   Shot Index: 0   Time Taken: 0.00017992973327636718    RAM used:  245.76
Beam Index: 0   Shot Index: 1   Time Taken: 0.00011997222900390625    RAM used:  0.0
Beam Index: 0   Shot Index: 2   Time Taken: 0.00013991355895996095    RAM used:  0.0
Beam Index: 0   Shot Index: 3   Time Taken: 0.0001484346389770508    RAM used:  0.0
Beam Index: 0   Shot Index: 4   Time Taken: 0.000139923095703125    RAM used:  0.0
Beam Index: 0   Shot Index: 5   Time Taken: 0.00015999794006347657    RAM used:  0.0
Beam Index: 0   Shot Index: 6   Time Taken: 0.00011992931365966796    RAM used:  0.0
Beam Index: 0   Shot Index: 7   Time Taken: 0.0001398944854736328    RAM used:  0.0
Beam Index: 0   Shot Index: 8   Time Taken: 0.00013994216918945313    RAM used:  0.0
Beam Index: 0   Shot Index: 9   Time Taken: 0.00015992164611816406    RAM used:  0.0
Beam Index: 0   Shot Index: 10   Time Taken: 0.000139923095703125    RAM used:  0.0
Beam Index: 0   Shot Index: 11   Time Taken: 0.00013992786407470703

Beam Index: 0   Shot Index: 108   Time Taken: 0.00017991065979003907    RAM used:  0.0
Beam Index: 0   Shot Index: 109   Time Taken: 9.992599487304688e-05    RAM used:  0.0
Beam Index: 0   Shot Index: 110   Time Taken: 0.00013995647430419921    RAM used:  0.0
Beam Index: 0   Shot Index: 111   Time Taken: 0.0001598072052001953    RAM used:  0.0
Beam Index: 0   Shot Index: 112   Time Taken: 0.0002598762512207031    RAM used:  0.0
Beam Index: 0   Shot Index: 113   Time Taken: 0.00015987396240234374    RAM used:  0.0
Beam Index: 0   Shot Index: 114   Time Taken: 0.00013991832733154297    RAM used:  0.0
Beam Index: 0   Shot Index: 115   Time Taken: 0.00019988536834716797    RAM used:  0.0
Beam Index: 0   Shot Index: 116   Time Taken: 0.00019989490509033202    RAM used:  0.0
Beam Index: 0   Shot Index: 117   Time Taken: 0.00013992786407470703    RAM used:  0.0
Beam Index: 0   Shot Index: 118   Time Taken: 0.0001598691940307617    RAM used:  0.0
Beam Index: 0   Shot Index: 119   Time Taken: 0

Beam Index: 0   Shot Index: 215   Time Taken: 0.00021982669830322265    RAM used:  0.0
Beam Index: 0   Shot Index: 216   Time Taken: 0.0001600027084350586    RAM used:  0.0
Beam Index: 0   Shot Index: 217   Time Taken: 0.00017991065979003907    RAM used:  0.0
Beam Index: 0   Shot Index: 218   Time Taken: 0.00021988868713378906    RAM used:  0.0
Beam Index: 0   Shot Index: 219   Time Taken: 0.00021991729736328124    RAM used:  0.0
Beam Index: 0   Shot Index: 220   Time Taken: 0.0002199697494506836    RAM used:  0.0
Beam Index: 0   Shot Index: 221   Time Taken: 0.00025986194610595704    RAM used:  0.0
Beam Index: 0   Shot Index: 222   Time Taken: 0.0002998065948486328    RAM used:  0.0
Beam Index: 0   Shot Index: 223   Time Taken: 0.0002398824691772461    RAM used:  0.0
Beam Index: 0   Shot Index: 224   Time Taken: 0.0001598978042602539    RAM used:  0.0
Beam Index: 0   Shot Index: 225   Time Taken: 0.00019996166229248048    RAM used:  0.0
Beam Index: 0   Shot Index: 226   Time Taken: 0.

Beam Index: 0   Shot Index: 316   Time Taken: 0.0002198648452758789    RAM used:  0.0
Beam Index: 0   Shot Index: 317   Time Taken: 0.0005198240280151368    RAM used:  0.0
Beam Index: 0   Shot Index: 318   Time Taken: 0.0004996490478515625    RAM used:  0.0
Beam Index: 0   Shot Index: 319   Time Taken: 0.00027982234954833986    RAM used:  0.0
Beam Index: 0   Shot Index: 320   Time Taken: 0.00045957565307617185    RAM used:  0.0
Beam Index: 0   Shot Index: 321   Time Taken: 0.0003618621826171875    RAM used:  0.0
Beam Index: 0   Shot Index: 322   Time Taken: 0.00029963016510009766    RAM used:  0.0
Beam Index: 0   Shot Index: 323   Time Taken: 0.0004198789596557617    RAM used:  0.0
Beam Index: 0   Shot Index: 324   Time Taken: 0.00023987770080566406    RAM used:  0.0
Beam Index: 0   Shot Index: 325   Time Taken: 0.00041972637176513673    RAM used:  0.0
Beam Index: 0   Shot Index: 326   Time Taken: 0.0003000450134277344    RAM used:  0.0
Beam Index: 0   Shot Index: 327   Time Taken: 0.0

Beam Index: 0   Shot Index: 413   Time Taken: 0.00017987251281738283    RAM used:  0.0
Beam Index: 0   Shot Index: 414   Time Taken: 0.0001999235153198242    RAM used:  0.0
Beam Index: 0   Shot Index: 415   Time Taken: 0.00015996456146240236    RAM used:  0.0
Beam Index: 0   Shot Index: 416   Time Taken: 0.00017993927001953126    RAM used:  0.0
Beam Index: 0   Shot Index: 417   Time Taken: 0.00013988494873046876    RAM used:  0.0
Beam Index: 0   Shot Index: 418   Time Taken: 9.993553161621094e-05    RAM used:  0.0
Beam Index: 0   Shot Index: 419   Time Taken: 0.00017991065979003907    RAM used:  0.0
Beam Index: 0   Shot Index: 420   Time Taken: 0.00011997699737548829    RAM used:  0.0
Beam Index: 0   Shot Index: 421   Time Taken: 5.997180938720703e-05    RAM used:  0.0
Beam Index: 0   Shot Index: 422   Time Taken: 0.00017987728118896485    RAM used:  0.0
Beam Index: 0   Shot Index: 423   Time Taken: 0.00027991294860839843    RAM used:  0.0
Beam Index: 0   Shot Index: 424   Time Taken: 

...

Beam Index: 7   Shot Index: 1816   Time Taken: 0.0002797698974609375    RAM used:  0.0
Beam Index: 7   Shot Index: 1817   Time Taken: 0.00032534122467041014    RAM used:  0.0
Beam Index: 7   Shot Index: 1818   Time Taken: 0.00021988868713378906    RAM used:  0.0
Beam Index: 7   Shot Index: 1819   Time Taken: 0.00045957565307617185    RAM used:  0.0
Beam Index: 7   Shot Index: 1820   Time Taken: 0.00023988723754882812    RAM used:  0.0
Beam Index: 7   Shot Index: 1821   Time Taken: 0.00023987770080566406    RAM used:  0.0
Beam Index: 7   Shot Index: 1822   Time Taken: 0.00021994590759277343    RAM used:  245.76
Beam Index: 7   Shot Index: 1823   Time Taken: 0.0005398368835449218    RAM used:  0.0
Beam Index: 7   Shot Index: 1824   Time Taken: 0.00025975704193115234    RAM used:  163.84
Beam Index: 7   Shot Index: 1825   Time Taken: 0.00019993782043457032    RAM used:  0.0
Beam Index: 7   Shot Index: 1826   Time Taken: 0.00021991252899169922    RAM used:  0.0
Beam Index: 7   Shot Index: 

Beam Index: 7   Shot Index: 1912   Time Taken: 0.00019989490509033202    RAM used:  81.92
Beam Index: 7   Shot Index: 1913   Time Taken: 0.0003198528289794922    RAM used:  0.0
Beam Index: 7   Shot Index: 1914   Time Taken: 0.00023983001708984374    RAM used:  0.0
Beam Index: 7   Shot Index: 1915   Time Taken: 0.00018199443817138673    RAM used:  0.0
Beam Index: 7   Shot Index: 1916   Time Taken: 0.00019994258880615234    RAM used:  0.0
Beam Index: 7   Shot Index: 1917   Time Taken: 0.00019988536834716797    RAM used:  0.0
Beam Index: 7   Shot Index: 1918   Time Taken: 0.00021988868713378906    RAM used:  0.0
Beam Index: 7   Shot Index: 1919   Time Taken: 0.00023990154266357423    RAM used:  0.0
Beam Index: 7   Shot Index: 1920   Time Taken: 0.00021991252899169922    RAM used:  163.84
Beam Index: 7   Shot Index: 1921   Time Taken: 0.00013988494873046876    RAM used:  0.0
Beam Index: 7   Shot Index: 1922   Time Taken: 0.00024062156677246094    RAM used:  0.0
Beam Index: 7   Shot Index: 

Beam Index: 7   Shot Index: 2013   Time Taken: 0.00020073413848876954    RAM used:  163.84
Beam Index: 7   Shot Index: 2014   Time Taken: 0.00021985530853271484    RAM used:  0.0
Beam Index: 7   Shot Index: 2015   Time Taken: 0.0004000091552734375    RAM used:  0.0
Beam Index: 7   Shot Index: 2016   Time Taken: 0.00019990921020507813    RAM used:  0.0
Beam Index: 7   Shot Index: 2017   Time Taken: 0.00023984909057617188    RAM used:  0.0
Beam Index: 7   Shot Index: 2018   Time Taken: 0.00017993450164794923    RAM used:  163.84
Beam Index: 7   Shot Index: 2019   Time Taken: 0.0002807474136352539    RAM used:  0.0
Beam Index: 7   Shot Index: 2020   Time Taken: 0.00023988723754882812    RAM used:  327.68
Beam Index: 7   Shot Index: 2021   Time Taken: 0.0001999044418334961    RAM used:  0.0
Beam Index: 7   Shot Index: 2022   Time Taken: 0.0002598714828491211    RAM used:  81.92
Beam Index: 7   Shot Index: 2023   Time Taken: 0.000259857177734375    RAM used:  0.0
Beam Index: 7   Shot Index:

Beam Index: 7   Shot Index: 2109   Time Taken: 0.00015993118286132811    RAM used:  0.0
Beam Index: 7   Shot Index: 2110   Time Taken: 0.00019993782043457032    RAM used:  0.0
Beam Index: 7   Shot Index: 2111   Time Taken: 0.00010003566741943359    RAM used:  0.0
Beam Index: 7   Shot Index: 2112   Time Taken: 0.00017991065979003907    RAM used:  0.0
Beam Index: 7   Shot Index: 2113   Time Taken: 0.00017996311187744142    RAM used:  0.0
Beam Index: 7   Shot Index: 2114   Time Taken: 0.00021989345550537108    RAM used:  0.0
Beam Index: 7   Shot Index: 2115   Time Taken: 0.00017993927001953126    RAM used:  0.0
Beam Index: 7   Shot Index: 2116   Time Taken: 0.00019989013671875    RAM used:  0.0
Beam Index: 7   Shot Index: 2117   Time Taken: 0.00019990921020507813    RAM used:  0.0
Beam Index: 7   Shot Index: 2118   Time Taken: 0.0002413797378540039    RAM used:  0.0
Beam Index: 7   Shot Index: 2119   Time Taken: 0.00021989345550537108    RAM used:  0.0
Beam Index: 7   Shot Index: 2120   T

NameError: name 'ram_start_cubic' is not defined

In [26]:
overall_ram_cubic

108204032

In [28]:
print("Number of exception waveforms found: ", len(exceptions_waveforms))
print("Percentage of exception waveforms found: ", len(exceptions_waveforms)*100/ (t + len(exceptions_waveforms)))

Number of exception waveforms found:  11792
Percentage of exception waveforms found:  33.24312133513757


In [29]:
r_squared_array_cubic = []
sum_rsq_cubic = 0.0

for i in range(len(interpolation_cubic)): # beam loop
    r_squared_array_beam_cubic = []
    
    for j in range(len(interpolation_cubic[i])): # shot loop
        r_squared_cubic = 0
        df_spline = wvDF_array[i][j]
        y = df_spline['Elevation (m)']

        for k in range(len(interpolation_cubic[i][j])): # each of 101 point in the shot
            r_squared_cubic += pow((interpolation_cubic[i][j][k] - y[k]), 2)

        sum_rsq_cubic += r_squared_cubic
            
        r_squared_array_beam_cubic.append(r_squared_cubic)
        
    r_squared_array_cubic.append(r_squared_array_beam_cubic)

In [31]:
print("Cubic Interpolation total r-squared value: ", sum_rsq_cubic)
print("Cubic Interpolation average r-squared value: ", sum_rsq_cubic / t)

Cubic Interpolation total r-squared value:  1.3882197041634871e-18
Cubic Interpolation average r-squared value:  5.862414291230942e-23


In [32]:
linear_greater_time = 0
for i in range(len(computer_usage_1d)):
    for j in range(len(computer_usage_1d[i])):

        if computer_usage_1d[i][j][0] > computer_usage_cubic[i][j][0]:
            linear_greater_time +=1

In [33]:
print("Number of values of Time for Linear Interpolation > Cubic Interpolation: ", linear_greater_time)
print("Percentage of Time for Linear Interpolation > Cubic Interpolation", (linear_greater_time / t) * 100)

Number of values of Time for Linear Interpolation > Cubic Interpolation:  17887
Percetages of Time for Linear Interpolation > Cubic Interpolation 75.53631756756756


In [ ]:
###############################################################################################################################
# INFERENCE

In [39]:
beam_index_final = []
shot_index_final = []

linear_time = []
linear_ram = []
linear_rsq = []

cubic_time = []
cubic_ram = []
cubic_rsq = []

for i in range(len(wvDF_array)):
    for j in range(len(wvDF_array[i])):
        beam_index_final.append(i+1)
        shot_index_final.append(j + 1)
        
        linear_time.append(computer_usage_1d[i][j][0])
        linear_ram.append(computer_usage_1d[i][j][1])
        linear_rsq.append(r_squared_array[i][j])
        
        cubic_time.append(computer_usage_cubic[i][j][0])
        cubic_ram.append(computer_usage_cubic[i][j][1])
        cubic_rsq.append(r_squared_array_cubic[i][j])

In [45]:
computer_usage_final  = pd.DataFrame({'Beam' : beam_index_final, 'Shot' : shot_index_final, 'L.I. Time (s)' : linear_time,
                                      'L.I. RAM (bytes)' : linear_ram, 'L.I. MSE' : linear_rsq, 'C.I. Time (s)' : cubic_time,
                                      'C.I. RAM (bytes)' : cubic_ram, 'C.I. MSE' : cubic_rsq})

In [47]:
computer_usage_final

Beam  Shot  L.I. Time (s)  L.I. RAM (bytes)  L.I. MSE  C.I. Time (s)  \
0         1     1        0.00020            983.04       0.0       0.000180   
1         1     2        0.00018              0.00       0.0       0.000120   
2         1     3        0.00018              0.00       0.0       0.000140   
3         1     4        0.00020              0.00       0.0       0.000148   
4         1     5        0.00020              0.00       0.0       0.000140   
...     ...   ...            ...               ...       ...            ...   
23675     8  2174        0.00026              0.00       0.0       0.000220   
23676     8  2175        0.00028              0.00       0.0       0.000280   
23677     8  2176        0.00040             81.92       0.0       0.000420   
23678     8  2177        0.00048              0.00       0.0       0.000220   
23679     8  2178        0.00028              0.00       0.0       0.000240   

       C.I. RAM (bytes)      C.I. MSE  
0                245.76  4.053185e-23  
1                  0.00  4.384057e-23  
2                  0.00  3.639595e-23  
3                  0.00  3.391441e-23  
4                  0.00  2.564260e-23  
...                 ...           ...  
23675              0.00  1.976962e-22  
23676            163.84  2.067952e-22  
23677              0.00  2.010049e-22  
23678              0.00  2.067952e-22  
23679              0.00  2.332649e-22  

[23680 rows x 8 columns]

In [60]:
computer_usage_final.to_csv('Results.csv', index=False)

In [63]:
print("total shots without exception waveforms: ", t)
print("total shots with exception waveforms: ", t + len(exceptions_waveforms))

print('\n\n')

print("Linear Interpolation total r-squared value: ", sum_rsq)
print("Linear Interpolation average r-squared value: ", sum_rsq / t)

print('\n')

print('Linear Interpolation entire process RAM usage: ', overall_ram_1d)
print('Linear Interpolation total RAM usage: ', sum(linear_ram))
print('Linear Interpolation average RAM usage: ', sum(linear_ram)/t)

print('\n')

print('Linear Interpolation total time: ', sum(linear_time))
print('Linear Interpolation average time: ', sum(linear_time)/t)

print('\n\n')

print("Cubic Interpolation total r-squared value: ", sum_rsq_cubic)
print("Cubic Interpolation average r-squared value: ", sum_rsq_cubic / t)

print('\n')

print('Cubic Interpolation entire process RAM usage: ', overall_ram_cubic)
print('Cubic Interpolation total RAM usage: ', sum(cubic_ram))
print('Cubic Interpolation average RAM usage: ', sum(cubic_ram)/t)

print('\n')

print('Cubic Interpolation total time: ', sum(cubic_time))
print('Cubic Interpolation average time: ', sum(cubic_time)/t)

print('\n')

print("Number of values of Time for Linear Interpolation > Cubic Interpolation: ", linear_greater_time)
print("Percentage of Time for Linear Interpolation > Cubic Interpolation: ", (linear_greater_time / t) * 100)

total shots without exception waveforms:  23680
total shots with exception waveforms:  35472



Linear Interpolation total r-squared value:  1.7904975090779743e-23
Linear Interpolation average r-squared value:  7.561222589011715e-28


Linear Interpolation entire process RAM usage:  98074624
Linear Interpolation total RAM usage:  1737850.8799999887
Linear Interpolation average RAM usage:  73.3889729729725


Linear Interpolation total time:  6.045272965431242
Linear Interpolation average time:  0.0002552902434726031



Cubic Interpolation total r-squared value:  1.3882197041634871e-18
Cubic Interpolation average r-squared value:  5.862414291230942e-23


Cubic Interpolation entire process RAM usage:  108204032
Cubic Interpolation total RAM usage:  236503.04000000388
Cubic Interpolation average RAM usage:  9.987459459459624


Cubic Interpolation total time:  4.896415433883705
Cubic Interpolation average time:  0.0002067743004173862


Number of values of Time for Linear Interpolation > Cubi

In [50]:
sum(linear_ram)

1737850.8799999887

In [51]:
overall_ram_1d

98074624

In [52]:
overall_ram_1d - sum(linear_ram)

96336773.12